In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [1]:
!pip install osmnx geopandas shapely pandas pyproj scikit-learn matplotlib folium hdbscan geopy meteostat


[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
# Importar librerías necesarias
import osmnx as ox
import geopandas as gpd
import pandas as pd
from shapely.geometry import Point
from pyproj import Transformer

import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import DBSCAN
import matplotlib.pyplot as plt

In [3]:
accidentes = pd.read_csv('../../2024_Accidentalidad.csv', sep=";")

# Verificar las columnas disponibles
print(accidentes.columns)
print(accidentes.head())

Index(['num_expediente', 'fecha', 'hora', 'localizacion', 'numero',
       'cod_distrito', 'distrito', 'tipo_accidente', 'estado_meteorológico',
       'tipo_vehiculo', 'tipo_persona', 'rango_edad', 'sexo', 'cod_lesividad',
       'lesividad', 'coordenada_x_utm', 'coordenada_y_utm', 'positiva_alcohol',
       'positiva_droga'],
      dtype='object')
  num_expediente       fecha      hora  \
0    2023S040280  04/01/2024  14:09:00   
1    2023S040280  04/01/2024  14:09:00   
2    2023S040309  15/02/2024  14:05:00   
3    2023S040309  15/02/2024  14:05:00   
4    2023S040310  18/02/2024  10:40:00   

                               localizacion numero  cod_distrito   distrito  \
0  AVDA. NICETO ALCALA ZAMORA / AUTOV. M-11      3            16  HORTALEZA   
1  AVDA. NICETO ALCALA ZAMORA / AUTOV. M-11      3            16  HORTALEZA   
2                CALL. TESORO / CALL. MINAS     18             1     CENTRO   
3                CALL. TESORO / CALL. MINAS     18             1     CENTRO   


In [4]:
# Crear un transformador para convertir de UTM Zona 30 a WGS84
transformer = Transformer.from_crs("EPSG:25830", "EPSG:4326", always_xy=True)

# Función para convertir coordenadas UTM a Lat/Lon
def utm_to_latlon(row):
    if pd.notnull(row["coordenada_x_utm"]) and pd.notnull(row["coordenada_y_utm"]):
        lon, lat = transformer.transform(row["coordenada_x_utm"], row["coordenada_y_utm"])
        return pd.Series([lat, lon])
    else:
        return pd.Series([None, None])

# Aplicar la conversión en nuevas columnas
accidentes[["latitud", "longitud"]] = accidentes.apply(utm_to_latlon, axis=1)

# Verificar que las nuevas columnas existen
print(accidentes[["latitud", "longitud"]].head())


     latitud  longitud
0  40.481706 -3.649939
1  40.481706 -3.649939
2  40.425009 -3.705860
3  40.425009 -3.705860
4  40.429974 -3.705746


In [5]:
# Eliminar filas con valores NaN en latitud o longitud
accidentes = accidentes.dropna(subset=["latitud", "longitud"])

# Crear geometría de puntos
accidentes["geometry"] = accidentes.apply(lambda row: Point(row["longitud"], row["latitud"]), axis=1)

# Convertir a GeoDataFrame con CRS WGS84
accidentes_gdf = gpd.GeoDataFrame(accidentes, geometry="geometry", crs="EPSG:4326")

# Mostrar los primeros datos transformados
print(accidentes_gdf.head())


  num_expediente       fecha      hora  \
0    2023S040280  04/01/2024  14:09:00   
1    2023S040280  04/01/2024  14:09:00   
2    2023S040309  15/02/2024  14:05:00   
3    2023S040309  15/02/2024  14:05:00   
4    2023S040310  18/02/2024  10:40:00   

                               localizacion numero  cod_distrito   distrito  \
0  AVDA. NICETO ALCALA ZAMORA / AUTOV. M-11      3            16  HORTALEZA   
1  AVDA. NICETO ALCALA ZAMORA / AUTOV. M-11      3            16  HORTALEZA   
2                CALL. TESORO / CALL. MINAS     18             1     CENTRO   
3                CALL. TESORO / CALL. MINAS     18             1     CENTRO   
4    GTA. RUIZ JIMENEZ / CALL. SAN BERNARDO      3             7   CHAMBERÍ   

            tipo_accidente estado_meteorológico            tipo_vehiculo  ...  \
0  Colisión fronto-lateral         Lluvia débil      Motocicleta > 125cc  ...   
1  Colisión fronto-lateral         Lluvia débil                  Turismo  ...   
2  Colisión fronto-lateral   

In [6]:
df = accidentes_gdf

In [7]:
# Antes de formatear la localizacion vamos a ver que forma tiene para saber como hacer la limpieza

df["localizacion"].dropna().sample(10, random_state=42).tolist()


['AUTOV. M-30, 20XC00',
 'CALL. OLVEGA, 26',
 'AUTOV. A-2, +00500E',
 'GTA. BILBAO / CALL. FUENCARRAL',
 'CALL. DOCTOR RAMON CASTROVIEJO / GTA. MARIANO SALVADOR MAELLA',
 'CALL. PEÑARANDA DE BRACAMONTE, 20A',
 "CALL. O'DONNELL, 21",
 'PLAZA. CONDE DE CASAL / CALL. CARLOS Y GUILLERMO FERNANDEZ SHAW',
 'AVDA. ENSANCHE DE VALLECAS / AUTOV. M-45',
 'CALL. SANTISIMA TRINIDAD / CALL. VIRIATO']

In [69]:
!pip install unidecode



[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [39]:
import pandas as pd
import numpy as np
import hdbscan
from sklearn.preprocessing import StandardScaler

# Asegurarse de que la columna 'hora' esté en formato datetime
df['hora'] = pd.to_datetime(df['hora'], format='%H:%M:%S')

# Convertir la hora a minutos desde medianoche
df['hora_minutos'] = df['hora'].dt.hour * 60 + df['hora'].dt.minute

# Filtrar filas con coordenadas NaN
df = df.dropna(subset=["latitud", "longitud", "hora_minutos"])

df["localizacion_limpia"] = df["localizacion"].apply(clean_localizacion)
df["localizacion_limpia"] = df["localizacion_limpia"].apply(refinar_localizacion_limpia)


# Convertir las coordenadas geográficas (latitud, longitud) a radianes
coords_geo = np.radians(df[["latitud", "longitud"]].values)

# Aplicar HDBSCAN con la métrica 'haversine' para las coordenadas geográficas
clusterer = hdbscan.HDBSCAN(min_cluster_size=10, metric="haversine")
cluster_labels = clusterer.fit_predict(coords_geo)

# Guardar los clusters en el DataFrame
df["cluster"] = cluster_labels

# Crear un resumen de los clusters (sin hora en la métrica)
df_cluster = df.groupby("cluster").agg(
    num_elementos=("cluster", "count"),
    media_latitud=("latitud", "mean"),
    media_longitud=("longitud", "mean"),
    max_hora=("hora_minutos", "max"),
    min_hora=("hora_minutos", "min")
).reset_index()

# Eliminar el cluster -1 (puntos considerados ruido)
df_cluster = df_cluster[df_cluster["cluster"] != -1]
# Añadir la lista de localizaciones por cluster
loc_por_cluster = df[df["cluster"] != -1].groupby("cluster")["localizacion_limpia"].apply(list).reset_index()
df_cluster = df_cluster.merge(loc_por_cluster, on="cluster")


df_cluster.head()




c:\Users\thelu\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\thelu\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


cluster  num_elementos  media_latitud  media_longitud  max_hora  min_hora  \
0        0             12      40.518647       -3.778271      1335        30   
1        1             13      40.428560       -3.576810      1075       855   
2        2             25      40.427044       -3.579117      1240       420   
3        3             51      40.353118       -3.570552      1270        45   
4        4             10      40.462859       -3.770520      1410       580   

                                 localizacion_limpia  
0  [[calle guardia civil 21], [calle guardia civi...  
1  [[carretera vicalvaro a coslada, avenida marco...  
2  [[avenida arcentales, avenida marconi], [aveni...  
3  [[m 50 34 via servicio], [m 50 34 via servicio...  
4  [[autovia m 500, autovia a 6], [autovia m 500,...

In [40]:
df_cluster.size

10262

In [12]:
import pandas as pd
import re
from unidecode import unidecode

def refinar_localizacion_limpia(lista_calles):
    if not isinstance(lista_calles, list):
        return []

    clean_list = []
    replacements = {
        "c,": "calle",
        "c.": "calle",
        "ctra.": "carretera",
        "inter.": "",
        "idb.": "",
        "pk": "",
        "s/n": "",
        "km": "",
        "p.k.": "",
        "autov.": "autovia",
        "av.": "avenida"
    }

    for entrada in lista_calles:
        # Si es una lista anidada (como [["calle a, calle b"]])
        if isinstance(entrada, list):
            subcalles = entrada
        else:
            subcalles = [entrada]

        for calle in subcalles:
            calle = calle.lower()
            calle = unidecode(calle)

            # Reemplazos
            for abbr, full in replacements.items():
                calle = calle.replace(abbr, full)

            # Eliminar caracteres raros
            calle = re.sub(r"[^a-z0-9áéíóúüñ ]", " ", calle)
            calle = re.sub(r"\s+", " ", calle).strip()

            # Evitar vacíos
            if calle and calle not in clean_list:
                clean_list.append(calle)

    return clean_list
    



In [13]:
df_cluster["localizacion_limpia"] = df_cluster["localizacion_limpia"].apply(refinar_localizacion_limpia)


In [41]:
!pip install haversine


[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [42]:
from haversine import haversine

def merge_close_clusters(df_cluster, distance_threshold_meters=20):
    merged_clusters = []
    visited = set()
    
    for idx, row in df_cluster.iterrows():
        if row["cluster"] in visited:
            continue

        group = [row["cluster"]]
        lat1, lon1 = row["media_latitud"], row["media_longitud"]

        for jdx, other in df_cluster.iterrows():
            if other["cluster"] in visited or other["cluster"] == row["cluster"]:
                continue

            lat2, lon2 = other["media_latitud"], other["media_longitud"]
            distance = haversine((lat1, lon1), (lat2, lon2)) * 1000  # Convert km to meters

            if distance < distance_threshold_meters:
                group.append(other["cluster"])
                visited.add(other["cluster"])

        # Agrega el cluster principal también
        visited.update(group)

        # Extrae y combina la info de todos los clusters del grupo
        sub_df = df_cluster[df_cluster["cluster"].isin(group)]

        merged_clusters.append({
            "cluster": min(group),
            "num_elementos": sub_df["num_elementos"].sum(),
            "media_latitud": sub_df["media_latitud"].mean(),
            "media_longitud": sub_df["media_longitud"].mean(),
            "max_hora": sub_df["max_hora"].max(),
            "min_hora": sub_df["min_hora"].min(),
            "localizacion_limpia": sum(sub_df["localizacion_limpia"], [])
        })

    return pd.DataFrame(merged_clusters)


In [43]:
df_cluster_merged = merge_close_clusters(df_cluster)

In [44]:
df_cluster_merged.size

10199

In [78]:
!pip install openpyxl



[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [45]:
df_estaciones = pd.read_excel('../Originales/ubicaciones trafico/pmed_ubicacion_10-2024.xlsx')

In [46]:
df_estaciones.head()

tipo_elem  distrito     id cod_cent                                  nombre  \
0       URB      11.0   5094    50404                 (TACTICO) GUADALETE E-O   
1       URB      11.0   3551    50406                 (TACTICO) NAVAHONDA O-E   
2       URB      11.0  11314    50407            (TACTICO) MIGUEL SORIANO E-O   
3       URB      11.0   5139    58008  PORTALEGRE O-E ENTRE OPORTO Y ABRANTES   
4       URB      11.0   5140    58009  FARO E-O ENTRE VÍA LUSITANA Y ABRANTES   

           utm_x         utm_y  longitud    latitud  
0  439225.835430  4.471196e+06 -3.716056  40.389144  
1  439283.029354  4.471616e+06 -3.715422  40.392933  
2  439305.621686  4.471490e+06 -3.715144  40.391797  
3  438562.312598  4.470700e+06 -3.723825  40.384629  
4  438377.184286  4.470303e+06 -3.725967  40.381038

## Limpieza nombre df_estaciones

In [47]:
def clean_nombre_estacion(nombre):
    if pd.isna(nombre):
        return ""

    nombre = nombre.upper()

    # Eliminar textos entre paréntesis
    nombre = re.sub(r"\s+", " ", nombre).strip()


    # Reemplazos comunes (igual que antes)
    replacements = {
        "CALL.": "calle",
        "AVDA.": "avenida",
        "AVD.": "avenida",
        "GTA.": "glorieta",
        "GLTA.": "glorieta",
        "PLAZA.": "plaza",
        "PLZA.": "plaza",
        "AUTOV.": "autovia",
        "PASEO.": "paseo",
        "BULEV.": "bulevar"
    }

    for abbr, full in replacements.items():
        nombre = nombre.replace(abbr, full)

    # Eliminar palabras y patrones irrelevantes
    eliminar = [
        "SALIDA", "ENTRADA", "GIRO", "IZDA", "DCHA", "IZQUIERDA", "DERECHA",
        "PK", "P.K.", "KM", "M-", "N-", "OESTE", "ESTE", "NORTE", "SUR"
    ]

    for palabra in eliminar:
        nombre = re.sub(rf"\b{palabra}\b", "", nombre)

    # Eliminar códigos (como o123, pm10021, etc.)
    nombre = re.sub(r"\b[a-zA-Z]{1,3}\d{2,5}\b", "", nombre)

    # Eliminar guiones múltiples y limpiar espacios
    nombre = nombre.replace("-", " ")
    nombre = re.sub(r"\s+", " ", nombre)
    nombre = unidecode(nombre.lower().strip())

    return nombre


In [48]:
df_estaciones["nombre_limpio"] = df_estaciones["nombre"].apply(clean_nombre_estacion)


In [49]:
from scipy.spatial import cKDTree

# Crear árbol KD con las coordenadas de las estaciones
tree = cKDTree(df_estaciones[["latitud", "longitud"]].values)

# Buscar la estación más cercana para cada cluster
distancias, indices = tree.query(df_cluster_merged[["media_latitud", "media_longitud"]].values)

# Agregar la columna con el ID de la estación más cercana
df_cluster_merged["id_estacion_proxima"] = df_estaciones.iloc[indices]["id"].values
df_cluster_merged["longitud_estacion"] = df_estaciones.iloc[indices]["longitud"].values
df_cluster_merged["latitud_estacion"] = df_estaciones.iloc[indices]["latitud"].values

# Solo columnas necesarias para el merge
df_estaciones_reducido = df_estaciones[["id", "nombre_limpio"]]

# Merge con df_cluster usando el ID de estación
# Volver a hacer merge para que tenga el nombre limpio actualizado
df_cluster_merged = df_cluster_merged.drop(columns=["nombre_estacion_proxima"], errors="ignore")

df_cluster_merged = df_cluster_merged.merge(
    df_estaciones[["id", "nombre_limpio"]],
    how="left",
    left_on="id_estacion_proxima",
    right_on="id"
).rename(columns={"nombre_limpio": "nombre_estacion_proxima"})


# Renombrar columna para más claridad
df_cluster_merged = df_cluster_merged.rename(columns={"nombre_limpio": "nombre_calle_estacion_proxima"})


print(df_cluster_merged.head())  # Ver resultado


   cluster  num_elementos  media_latitud  media_longitud  max_hora  min_hora  \
0        0             12      40.518647       -3.778271      1335        30   
1        1             13      40.428560       -3.576810      1075       855   
2        2             25      40.427044       -3.579117      1240       420   
3        3             51      40.353118       -3.570552      1270        45   
4        4             10      40.462859       -3.770520      1410       580   

                                 localizacion_limpia  id_estacion_proxima  \
0  [[calle guardia civil 21], [calle guardia civi...                 3680   
1  [[carretera vicalvaro a coslada, avenida marco...                 6548   
2  [[avenida arcentales, avenida marconi], [aveni...                 6548   
3  [[m 50 34 via servicio], [m 50 34 via servicio...                 5380   
4  [[autovia m 500, autovia a 6], [autovia m 500,...                 4890   

   longitud_estacion  latitud_estacion    id  \
0       

In [50]:
!pip install rapidfuzz


[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [61]:
def best_matching_score_v3(row):
    from rapidfuzz import fuzz
    from unidecode import unidecode

    # Prepara nombre de estación
    nombre_estacion = row["nombre_estacion_proxima"]
    if pd.isna(nombre_estacion):
        return 0

    nombre_estacion = unidecode(nombre_estacion.lower())
    nombre_estacion = re.sub(r"\(.*?\)", "", nombre_estacion)
    nombre_estacion = re.sub(r"\b(?:s\.?n\.?|e\s?o|norte|sur|este|oeste|frente|delante|tactico|alde\.?|pm\d+)\b", "", nombre_estacion)
    partes_estacion = [p.strip() for p in re.split(r"[-,/]", nombre_estacion) if p.strip()]

    # Asegura que las calles sean una lista plana
    calles_cluster = row["localizacion_limpia"]
    if not calles_cluster or not isinstance(calles_cluster, list):
        return 0
    calles_flat = [item for sublist in calles_cluster for item in (sublist if isinstance(sublist, list) else [sublist])]

    # Comparar cada parte de la estación contra cada calle
    scores = []
    for parte in partes_estacion:
        for calle in calles_flat:
            calle = unidecode(calle.lower())
            s1 = fuzz.token_set_ratio(parte, calle)
            s2 = fuzz.partial_ratio(parte, calle)
            scores.append(max(s1, s2))

    return max(scores) if scores else 0


In [62]:
df_cluster_merged["score_estacion_vs_calles"] = df_cluster_merged.apply(best_matching_score_v3, axis=1)


In [63]:
import folium
from folium.plugins import MarkerCluster

points = df_cluster_merged[["media_latitud", "media_longitud"]].values.tolist()
points_estaciones = df_cluster_merged[["latitud_estacion", "longitud_estacion"]].values.tolist()

m = folium.Map(location=[40, 0], zoom_start=6)
for point in points:
  folium.CircleMarker( location=[point[0], point[1]], radius=5, color="red", fill=True, fill_color="red", popup='', ).add_to(m)
for point in points_estaciones:
  folium.CircleMarker( location=[point[0], point[1]], radius=5, color="green", fill=True, fill_color="green", popup='', ).add_to(m)
for point1,point2 in zip(points,points_estaciones):
  folium.PolyLine(locations=[point1,point2],color="blue").add_to(m)


In [64]:
df_cluster_merged[["cluster", "nombre_estacion_proxima", "localizacion_limpia", "score_estacion_vs_calles"]].sort_values("score_estacion_vs_calles", ascending=False).head(10)


cluster                            nombre_estacion_proxima  \
1456     1465                  alcala e o(pl. cibeles barquillo)   
1437     1444                 gran via,25 o e(salud tres cruces)   
1429     1436                     alcala e o(gran via cedaceros)   
1427     1434      (aforos) hortaleza, 11 s n(gran via infantas)   
1426     1433  mendez alvaro e o (inferior 30) (entrevias ret...   
29         29  niceto alcala zamora, 11 miguel angel asturias...   
1423     1430       clavel, 1 s n (caballero de gracia gran via)   
1418     1425  (aforos) san bernardo, 15 e o(gran via pl. san...   
1416     1423                  atocha e o(san pedro san eugenio)   
1415     1422                  atocha e o(san pedro san eugenio)   

                                    localizacion_limpia  \
1456  [[paseo prado, plaza cibeles], [paseo prado, p...   
1437  [[calle gran via 30], [calle gran via 25], [ca...   
1429  [[calle alcala 45], [calle alcala 45], [calle ...   
1427  [[calle gran via, calle hortaleza], [calle gra...   
1426  [[autovia m 30 10nl94], [autovia m 30 10nl94],...   
29    [[avenida francisco javier saenz de oiza, call...   
1423  [[calle gran via, calle clavel], [calle gran v...   
1418  [[calle silva, calle san bernardo], [calle sil...   
1416  [[calle atocha, plaza emperador carlos v], [pa...   
1415  [[paseo prado, calle atocha], [paseo prado, ca...   

      score_estacion_vs_calles  
1456                     100.0  
1437                     100.0  
1429                     100.0  
1427                     100.0  
1426                     100.0  
29                       100.0  
1423                     100.0  
1418                     100.0  
1416                     100.0  
1415                     100.0

In [65]:
df_cluster_merged[df_cluster_merged["score_estacion_vs_calles"] < 50][["cluster", "nombre_estacion_proxima", "localizacion_limpia", "score_estacion_vs_calles"]].sample(10)


cluster                            nombre_estacion_proxima  \
995       997                      av. entrevias serena benameji   
141       141                                                      
1050     1052  conde penalver s( a maldonado) (diego de leon ...   
845       847    capitan blanco argibay s mundillo bravo murillo   
632       634  cno. hormigueras cno. hormigueras (entrevias) ...   
45         45      ronda del cooperativa electrica av. entrevias   
1325     1330                                                      
1349     1356  fray luis de leon s n(palos frontera ronda val...   
617       619                                                      
61         61                    planeta av. general av. logrono   

                                    localizacion_limpia  \
995   [[calle puerto de balbaran, calle candilejas],...   
141   [[autovia m 30 20nc00], [autovia m 30 20nc00],...   
1050  [[calle francisco silvela, calle diego de leon...   
845   [[calle veza, calle santa valentina], [calle v...   
632   [[calle puerto de balbaran, avenida entrevias]...   
45    [[avenida madrid mercamadrid, avenida legazpi ...   
1325  [[autovia m 30 c2 11 300], [autovia m 30 c2 11...   
1349  [[ronda atocha 34], [ronda atocha 34], [ronda ...   
617   [[autovia m 30 calzada 2 32 200], [autovia m 3...   
61    [[metro aeropuerto t1 t2 t3 0], [metro aeropue...   

      score_estacion_vs_calles  
995                  42.424242  
141                   0.000000  
1050                 48.275862  
845                  43.750000  
632                  46.511628  
45                   49.382716  
1325                  0.000000  
1349                 47.058824  
617                   0.000000  
61                   40.000000

In [66]:
df["localizacion_limpia"] = df["localizacion"].apply(clean_localizacion)
df["localizacion_limpia"] = df["localizacion_limpia"].apply(refinar_localizacion_limpia)


In [67]:
df_cluster_merged[["cluster", "localizacion_limpia"]].sample(5)


cluster                                localizacion_limpia
1308     1312  [[autovia m 30 11xc80], [autovia m 30 11xc80],...
28         28  [[carretera barrio de la fortuna, calle pinar ...
349       350  [[calle san narciso 15], [calle san narciso 15...
60         60  [[calle estefanita 3], [calle estefanita 3], [...
420       421  [[calle san jaime 7], [calle puerto de las pil...

In [68]:
df_cluster_merged[["nombre_estacion_proxima"]].drop_duplicates().sample(10)


nombre_estacion_proxima
1118        gral. ricardos o e(paulina odiaga penafiel)
250                    (micro) intercambiador autobuses
687           av. pablo neruda av. albufera luis bunuel
909   av. reina victoria o e gral. ibanez ibero pabl...
1000       general peron o e orense poeta joan maragall
670   (tactico) lopez mezquia, 5 e o (castellflorite...
1169                         misterios misterios alcala
958                           av. entrevias peal serena
522   (tactico) santiago de compostela e o fco. llor...
116                         arrastaria aracne samaniego

In [70]:
def limpiar_autovia(nombre):
    if pd.isna(nombre):
        return ""
    nombre = unidecode(nombre.lower())
    nombre = re.sub(r"\bautov\.\b", "autovia", nombre)
    nombre = re.sub(r"m[\s\-]?(\d{2})", r"m\1", nombre)
    nombre = re.sub(r"\b(pk|km|entrada|salida|calzada|lateral|interior|exterior|p\.k\.)\b", "", nombre)
    nombre = re.sub(r"\d+[a-z]*", "", nombre)
    nombre = re.sub(r"[^a-z0-9\s]", "", nombre)
    nombre = re.sub(r"\s+", " ", nombre).strip()
    return nombre


In [71]:
from scipy.spatial import cKDTree
from rapidfuzz import fuzz

def encontrar_mejor_estacion(cluster_row, estaciones_df, k=3):
    cluster_coord = [cluster_row["media_latitud"], cluster_row["media_longitud"]]
    tree = cKDTree(estaciones_df[["latitud", "longitud"]].values)
    dists, idxs = tree.query(cluster_coord, k=k)

    calles_cluster = cluster_row["localizacion_limpia"]
    if not calles_cluster:
        return None, None, 0

    # Flatten calles
    calles_flat = [item for sub in calles_cluster for item in (sub if isinstance(sub, list) else [sub])]
    calles_flat = [limpiar_autovia(c) for c in calles_flat]

    best_score = 0
    best_idx = None

    for i in range(k):
        est_row = estaciones_df.iloc[idxs[i]]
        nombre_est = limpiar_autovia(est_row["nombre_limpio"])
        for calle in calles_flat:
            score = fuzz.token_set_ratio(nombre_est, calle)
            if score > best_score:
                best_score = score
                best_idx = idxs[i]

    if best_idx is not None:
        est = estaciones_df.iloc[best_idx]
        return est["id"], est["latitud"], est["longitud"], est["nombre_limpio"], best_score
    else:
        return None, None, None, None, 0


In [72]:
# Prepara columnas
ids, lats, lons, nombres, scores = [], [], [], [], []

for _, row in df_cluster_merged.iterrows():
    id_est, lat, lon, nom, sc = encontrar_mejor_estacion(row, df_estaciones, k=3)
    ids.append(id_est)
    lats.append(lat)
    lons.append(lon)
    nombres.append(nom)
    scores.append(sc)

df_cluster_merged["id_estacion_mejor"] = ids
df_cluster_merged["latitud_estacion_mejor"] = lats
df_cluster_merged["longitud_estacion_mejor"] = lons
df_cluster_merged["nombre_estacion_mejor"] = nombres
df_cluster_merged["score_estacion_nombre"] = scores


In [86]:
# Esto lo hago porque antes las autovias no las detectaba bien por el nombre de calle y no hacian match

def contiene_autovia(calles):
    if not calles:
        return False
    autovias = ["m30", "m40", "a42", "a2", "a5"]
    for sub in calles:
        for calle in (sub if isinstance(sub, list) else [sub]):
            calle_limpia = limpiar_autovia(calle)
            if any(a in calle_limpia for a in autovias):
                return True
    return False

df_cluster_merged["es_autovia"] = df_cluster_merged["localizacion_limpia"].apply(contiene_autovia)

# Marcar los válidos
df_cluster_merged["match_valido"] = (df_cluster_merged["score_estacion_nombre"] >= 75) | df_cluster_merged["es_autovia"]

# Filtrar los no confiables
df_final = df_cluster_merged[df_cluster_merged["match_valido"]]


In [83]:
df_final[["cluster", "nombre_estacion_mejor", "score_estacion_nombre", "es_autovia"]].sort_values("score_estacion_nombre", ascending=False).head(10)


cluster                              nombre_estacion_mejor  \
27         27  av. fuerzas armadas (carril bus) estacion vald...   
1020     1022  toledo s juan antonio vallejo najera botas glo...   
1015     1017  (aforos)gran via san francisco s n(s.bernabe c...   
1016     1018  eduardo dato, 12 e o glorieta ruben dario alfo...   
1029     1031   ribera de curtidores s(mira el sol ronda toledo)   
1018     1020          po yeserias e o melilla glorietapiramides   
131       131  bulevar jose prat ladera de los almendros bule...   
125       125            av. mediterraneo acceso a 3 puentelarra   
133       133  bulevar jose prat bulevar indalecio prieto cor...   
994       996              ronda de segovia s(algeciras segovia)   

      score_estacion_nombre  es_autovia  
27                    100.0       False  
1020                  100.0       False  
1015                  100.0       False  
1016                  100.0       False  
1029                  100.0       False  
1018                  100.0       False  
131                   100.0       False  
125                   100.0       False  
133                   100.0       False  
994                   100.0       False

In [84]:
df_cluster_merged["match_tipo"] = df_cluster_merged.apply(
    lambda row: "por nombre" if row["score_estacion_nombre"] >= 75 else
                "autovia" if row["es_autovia"] else
                "descartado", axis=1
)

df_cluster_merged["match_tipo"].value_counts()


match_tipo
por nombre    925
descartado    532
Name: count, dtype: int64

### Juntar clusters por metros

In [87]:
from sklearn.neighbors import BallTree
import numpy as np
import pandas as pd

def merge_clusters_por_distancia(df, lat_col="media_latitud", lon_col="media_longitud", distancia_m=20):
    # Convertir coordenadas a radianes
    coords = np.radians(df[[lat_col, lon_col]].values)
    tree = BallTree(coords, metric="haversine")
    radio = distancia_m / 6371000  # 6371 km es el radio de la tierra

    # Vecinos dentro del radio
    vecinos = tree.query_radius(coords, r=radio)

    # Agrupar conectados
    visitados = set()
    grupos = []

    for i, vecinos_i in enumerate(vecinos):
        if i in visitados:
            continue
        grupo = set(vecinos_i)
        cola = list(vecinos_i)
        while cola:
            j = cola.pop()
            if j not in visitados:
                visitados.add(j)
                nuevos = set(vecinos[j])
                if not nuevos.issubset(grupo):
                    cola.extend(nuevos - grupo)
                    grupo |= nuevos
        grupos.append(list(grupo))

    # Construir nuevo DataFrame fusionado
    fusionados = []
    for grupo in grupos:
        sub_df = df.iloc[grupo]
        row = {
            "cluster_ids": sub_df["cluster"].tolist(),
            "media_latitud": sub_df[lat_col].mean(),
            "media_longitud": sub_df[lon_col].mean(),
            "localizacion_limpia": sum(sub_df["localizacion_limpia"], []),
            "id_estacion_mejor": sub_df["id_estacion_mejor"].mode()[0],
            "latitud_estacion_mejor": sub_df["latitud_estacion_mejor"].mean(),
            "longitud_estacion_mejor": sub_df["longitud_estacion_mejor"].mean(),
            "nombre_estacion_mejor": sub_df["nombre_estacion_mejor"].mode()[0],
            "score_estacion_nombre": sub_df["score_estacion_nombre"].max()
        }
        fusionados.append(row)

    return pd.DataFrame(fusionados)


In [95]:
df_fusionado = merge_clusters_por_distancia(df_final, distancia_m=30)


### ESTE ES SOLO PARA QUE SE VEA CUALES COGE Y CUALES NO, SOLO COGE LOS VERDES

In [108]:
import folium

# Crear el mapa centrado en el centroide general
centro_lat = df_cluster_merged["media_latitud"].mean()
centro_lon = df_cluster_merged["media_longitud"].mean()
m = folium.Map(location=[centro_lat, centro_lon], zoom_start=12)

# Función para asignar color por score
def get_color(score):
    if score >= 75:
        return "green"   # 🟢 Buen match
    elif score >= 50:
        return "orange"  # 🟡 Dudoso
    else:
        return "red"     # 🔴 Malo

# Añadir marcadores de clusters y sus estaciones
for _, row in df_cluster_merged.iterrows():
    color = get_color(row["score_estacion_vs_calles"])

    # Marcador del cluster (color según score)
    folium.CircleMarker(
        location=[row["media_latitud"], row["media_longitud"]],
        radius=5,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.9,
        popup=folium.Popup(f"""
            <b>Cluster:</b> {row["cluster"]}<br>
            <b>Estación:</b> {row["nombre_estacion_proxima"]}<br>
            <b>Score:</b> {row["score_estacion_vs_calles"]}
        """, max_width=300),
    ).add_to(m)

    # Marcador de la estación (verde fijo)
    folium.CircleMarker(
        location=[row["latitud_estacion"], row["longitud_estacion"]],
        radius=4,
        color="blue",
        fill=True,
        fill_color="blue",
        fill_opacity=0.5
    ).add_to(m)

    # Línea azul entre cluster y estación
    folium.PolyLine(
        locations=[
            [row["media_latitud"], row["media_longitud"]],
            [row["latitud_estacion"], row["longitud_estacion"]],
        ],
        color="blue",
        weight=1
    ).add_to(m)

# Mostrar el mapa
m


### Este es el final que usamos

In [96]:
import folium

centro_lat = df_fusionado["media_latitud"].mean()
centro_lon = df_fusionado["media_longitud"].mean()
m = folium.Map(location=[centro_lat, centro_lon], zoom_start=12)

def get_color(score):
    if score >= 75:
        return "green"
    elif score >= 50:
        return "orange"
    else:
        return "red"

for _, row in df_fusionado.iterrows():
    color = get_color(row["score_estacion_nombre"])

    folium.CircleMarker(
        location=[row["media_latitud"], row["media_longitud"]],
        radius=5,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.9,
        popup=folium.Popup(f"""
            <b>Cluster:</b> {row["cluster_ids"]}<br>
            <b>Estación:</b> {row["nombre_estacion_mejor"]}<br>
            <b>Score:</b> {row["score_estacion_nombre"]}
        """, max_width=300)
    ).add_to(m)

    folium.CircleMarker(
        location=[row["latitud_estacion_mejor"], row["longitud_estacion_mejor"]],
        radius=4,
        color="blue",
        fill=True,
        fill_color="blue",
        fill_opacity=0.5
    ).add_to(m)

    folium.PolyLine(
        locations=[
            [row["media_latitud"], row["media_longitud"]],
            [row["latitud_estacion_mejor"], row["longitud_estacion_mejor"]]
        ],
        color="blue",
        weight=1
    ).add_to(m)

m


In [99]:
trafico_2024 = pd.read_csv('../trafico_2024_completo.csv', sep=";")

In [100]:
print(trafico_2024.head())

     id           fecha_hora tipo_elem  intensidad  ocupacion  carga  vmed  \
0  1001  2024-01-01 13:00:00       C30        1560        4.0      0  61.0   
1  1001  2024-01-01 13:15:00       C30        1728        4.0      0  60.0   
2  1001  2024-01-01 13:30:00       C30        1800        5.0      0  58.0   
3  1001  2024-01-01 13:45:00       C30        1704        5.0      0  58.0   
4  1001  2024-01-01 14:00:00       C30        1812        5.0      0  58.0   

  error  periodo_integracion   hora  mes trimestre    latitud  longitud  
0     N                    5  13:00    1        Q1  40.409729 -3.740786  
1     N                    5  13:15    1        Q1  40.409729 -3.740786  
2     N                    5  13:30    1        Q1  40.409729 -3.740786  
3     N                    5  13:45    1        Q1  40.409729 -3.740786  
4     N                    5  14:00    1        Q1  40.409729 -3.740786  


In [101]:
df_fusionado["num_elementos"] = df_fusionado["cluster_ids"].apply(len)


In [103]:
# Asegurar formato HH:MM y convertir a minutos desde medianoche
trafico_2024["hora"] = trafico_2024["hora"].astype(str).str[:5]
trafico_2024["hora_minutos"] = (
    trafico_2024["hora"].str.split(":").str[0].astype(int) * 60 +
    trafico_2024["hora"].str.split(":").str[1].astype(int)
)

# Si no tienes min_hora y max_hora, puedes usar todo el día:
min_hora_default = 0
max_hora_default = 1440

# Inicializar columna
df_fusionado["suma_intensidad"] = 0

# Recorrer cada cluster fusionado
for index, row in df_fusionado.iterrows():
    estacion = row["id_estacion_mejor"]
    
    filtro = (
        (trafico_2024["id"] == estacion) &
        (trafico_2024["hora_minutos"] >= min_hora_default) &
        (trafico_2024["hora_minutos"] <= max_hora_default)
    )

    suma = trafico_2024.loc[filtro, "intensidad"].sum()
    df_fusionado.at[index, "suma_intensidad"] = suma




In [106]:
# Calcular probabilidad
df_fusionado["probabilidad_accidente"] = df_fusionado["num_elementos"] / df_fusionado["suma_intensidad"].replace(0, np.nan)
df_fusionado

cluster_ids  media_latitud  media_longitud  \
0           [5]      40.473401       -3.832465   
1          [12]      40.453450       -3.781125   
2          [13]      40.460819       -3.791483   
3          [16]      40.455044       -3.785334   
4          [18]      40.458954       -3.787998   
..          ...            ...             ...   
914      [1454]      40.420272       -3.704953   
915      [1456]      40.421613       -3.707966   
916      [1457]      40.422442       -3.709335   
917      [1458]      40.421096       -3.692057   
918      [1459]      40.421958       -3.691818   

                                   localizacion_limpia  id_estacion_mejor  \
0    [[avenida victoria 63], [avenida victoria 63],...             6635.0   
1    [[calle arroyo de pozuelo 99], [carretera hume...             4874.0   
2    [[calle ana teresa 85b], [calle ana teresa 85b...             4878.0   
3    [[calle golondrina calle brujula], [calle golo...             4883.0   
4    [[avenida osa mayor, calle pico ocejon], [aven...            10512.0   
..                                                 ...                ...   
914  [[calle concepcion arenal, calle gran via], [c...            10387.0   
915  [[calle san bernardo 10], [calle san bernardo ...             4295.0   
916  [[calle isabel la catolica 12], [calle isabel ...            11207.0   
917  [[paseo recoletos 8], [paseo recoletos 8], [pa...             4244.0   
918  [[paseo recoletos, calle prim], [paseo recolet...             3842.0   

     latitud_estacion_mejor  longitud_estacion_mejor  \
0                 40.473565                -3.832920   
1                 40.452493                -3.780809   
2                 40.461273                -3.791521   
3                 40.454831                -3.785388   
4                 40.459246                -3.787560   
..                      ...                      ...   
914               40.420283                -3.705074   
915               40.420761                -3.708260   
916               40.422154                -3.709360   
917               40.421417                -3.692061   
918               40.422132                -3.691727   

                                 nombre_estacion_mejor  score_estacion_nombre  \
0      av. victoria o e (av. estacion domingo alvarez)              76.190476   
1    arroyo pozuelo o98 e o (glorieta rio zancara h...              75.675676   
2    cno. del barrial o63 s (f. lazaro carreter alm...              75.000000   
3       golondrina o22 s n (escultor peresejo brujula)              85.714286   
4    av. osa mayor o102 e o (glorieta maria reina p...              78.571429   
..                                                 ...                    ...   
914   gran via, 40 e o (concepcion arenal miguel moya)              85.000000   
915   san bernardo, 15 o e(pl. santo domingo gran via)              80.000000   
916                                     gran via s (+)              88.888889   
917                   po recoletos s(prim pl. cibeles)              75.000000   
918                      po recoletos s almirante prim              75.000000   

     num_elementos  suma_intensidad  probabilidad_accidente  
0                1          3328435            3.004415e-07  
1                1          1992952            5.017682e-07  
2                1          3100480            3.225307e-07  
3                1          2193224            4.559498e-07  
4                1           744481            1.343218e-06  
..             ...              ...                     ...  
914              1          7749858            1.290346e-07  
915              1          3065265            3.262361e-07  
916              1                0                     NaN  
917              1         13044367            7.666144e-08  
918              1         11768865            8.496996e-08  

[919 rows x 12 columns]

In [107]:
# Ver top 10
top_10 = df_fusionado.nlargest(10, "probabilidad_accidente")
print(top_10)

    cluster_ids  media_latitud  media_longitud  \
615       [955]      40.451926       -3.686009   
62        [126]      40.382316       -3.603348   
26         [58]      40.483079       -3.649246   
85        [173]      40.463249       -3.621228   
30         [77]      40.366509       -3.654632   
5          [21]      40.483044       -3.633092   
8          [27]      40.483316       -3.616773   
293       [476]      40.364546       -3.753671   
14         [36]      40.354309       -3.712331   
633       [982]      40.445205       -3.691030   

                                   localizacion_limpia  id_estacion_mejor  \
615  [[calle padre damian 2], [calle padre damian 2...             3448.0   
62   [[calle cerro de almodovar 9], [calle cerro de...             5211.0   
26   [[avenida niceto alcala zamora, calle pintor l...            11105.0   
85   [[glorieta praga 0], [glorieta praga 0], [aven...            10869.0   
30   [[carretera villaverde a vallecas 280], [carre...          